In [1]:
from pathlib import Path
from tqdm.auto import tqdm

import pandas as pd
import torch

import hvplot.pandas

import xtensor as xt
import diffhydro as dh
import diffhydro.pipelines as dhp

from utils import load_fr_data, split_and_normalize_data

In [2]:
N = 10             # Repeat experiment 10 times
lr = .005          # Initial Runoff Learning rate
wd = .001          # LSTM Weight decay

n_epoch = 5      # training epoch
n_iter = 40        # Iteration per epoch

init_window = 365
pred_len = 20

device = "cuda:7" # Device: Assume available to NVIDIA GPU
irf_fns = "hayami"

root = Path("./data/dataset")

In [3]:
batch_size=8
clip_grad_norm=1
routing_lr=10**-4
routing_wd=10**-3
runoff_lr=.005
runoff_wd=.001
dt=1/24
max_delay=100
scheduler_step_size=10
scheduler_gamma=.3

### Data loading

In [4]:
g, kp, inp_stat, inp_dyn, lbl, statics = load_fr_data(root, device)
inp_tr, inp_te, lbl_tr, lbl_te, lbl_std = split_and_normalize_data(inp_dyn, lbl)

In [5]:
tr_ds  = dhp.BaseDataset(x=inp_tr, y=lbl_tr, g=g, 
                         init_len=init_window, 
                         pred_len=pred_len, 
                         statics=statics)
val_ds = dhp.BaseDataset(x=inp_te, y=lbl_te, g=g, 
                         init_len=init_window, 
                         pred_len=pred_len, 
                         statics=statics) 

In [6]:
inp_mlp_size = 1
inp_lstm_size = 288

param_model = dhp.utils.MLP(inp_mlp_size,2)
model = dhp.RunoffRoutingModel(param_model, input_size=inp_lstm_size, 
                               dt=dt, max_delay=max_delay,
                               temp_res_h=24).to(device)

module = dhp.RunoffRoutingModule(model, tr_ds, val_ds,
                                 batch_size=batch_size,
                                 device=device,
                                 clip_grad_norm=clip_grad_norm,
                                 routing_lr=routing_lr, 
                                 routing_wd=routing_wd, 
                                 runoff_lr=runoff_lr, 
                                 runoff_wd=runoff_wd,
                                 scheduler_step_size=scheduler_step_size,
                                 scheduler_gamma=scheduler_gamma)

In [ ]:
n_epoch = 20
n_iter = 100

tr_loss, val_loss = module.train(n_epoch=n_epoch, n_iter=n_iter)

0it [00:00, ?it/s]

  0%|          | 0/71 [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/71 [00:00<?, ?it/s]

0it [00:00, ?it/s]

...

  0%|          | 0/71 [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/71 [00:00<?, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/71 [00:00<?, ?it/s]

In [ ]:
tr_loss.hvplot(label="Training") * val_loss.hvplot(label="Validation")

In [ ]:
yte, ote = module.extract_val(device=device, batch_size=batch_size)
ytr, otr = module.extract_train(device=device, batch_size=batch_size)

nse_te = 1-(((yte-ote)**2).mean("time") / yte.var("time"))
nse_tr = 1-(((ytr-otr)**2).mean("time") / ytr.var("time"))

print(f"Training NSE: {nse_te.mean().item()}, Validation NSE: {nse_tr.mean().item()}")

ytr.hvplot.line(x="time", groupby="spatial", label="Observation") *\
otr.hvplot.line(x="time", groupby="spatial", label="Output") 

In [ ]:
params = model.routing_model.read_params(g.to(device), statics["channel_dist"].to(device))
irf_kernel_stable_hayami(params, time_window=max_delay, dt=dt)

In [12]:
import torch
import math
from diffroute.irfs import IRF_FN
import numpy as np

In [13]:
#params[:,-1]=20
#params[:,-2]=.1
#g.nodes_idx[pd.Series(dict(g.g.out_degree)).idxmin()]

In [9]:
#np.where(dego.index==dego.idxmin())

In [10]:
params = model.routing_model.read_params(g.to(device), statics["channel_dist"].to(device))

In [11]:
params

tensor([[  5.4900,   3.3182, 164.7382],
        [  0.9900,   3.2917, 165.1547],
        [  4.7700,   3.2898, 165.3521],
        ...,
        [  0.5400,   3.3184, 164.8154],
        [  4.2300,   3.3184, 164.8030],
        [  1.0800,   3.3184, 164.8160]], device='cuda:7',
       grad_fn=<CatBackward0>)

In [13]:
#params[:,1:]=model.routing_model.offset
#params

In [20]:
#pd.DataFrame(irf_kernel_linear_diffusion(params, time_window=max_delay, dt=dt)[:20].cpu().detach().t()).hvplot()
#pd.DataFrame(irf_kernel_stable_hayami(params, time_window=max_delay, dt=dt)[:20].cpu().detach().t()).hvplot()

In [17]:
param=params
time_window=max_delay
dt=dt

In [18]:
L, D, c = [x.unsqueeze(-1) for x in param.t()]
t = torch.arange(1, time_window * int(1/dt)+1, 
                 device=param.device, 
                 dtype=param.dtype)[None] * dt 
# Hayami formula
h = L / (2.0 * torch.sqrt(torch.pi * D * t**3))
exponent = -((L - c * (t-dt))**2) / (4.0 * D * t)

In [35]:
c*(t-dt)

tensor([[0.0000e+00, 6.9465e+00, 1.3893e+01,  ..., 1.6651e+04, 1.6658e+04,
         1.6665e+04],
        [0.0000e+00, 6.7624e+00, 1.3525e+01,  ..., 1.6210e+04, 1.6216e+04,
         1.6223e+04],
        [0.0000e+00, 6.7494e+00, 1.3499e+01,  ..., 1.6178e+04, 1.6185e+04,
         1.6192e+04],
        ...,
        [0.0000e+00, 6.9495e+00, 1.3899e+01,  ..., 1.6658e+04, 1.6665e+04,
         1.6672e+04],
        [0.0000e+00, 6.9492e+00, 1.3898e+01,  ..., 1.6657e+04, 1.6664e+04,
         1.6671e+04],
        [0.0000e+00, 6.9495e+00, 1.3899e+01,  ..., 1.6658e+04, 1.6665e+04,
         1.6672e+04]], device='cuda:7', grad_fn=<MulBackward0>)

In [39]:
((L-c*(t-dt))**2).argmin(dim=1)

tensor([1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 2, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1,
        1, 1, 1, 0, 1, 0, 1, 1, 2, 0, 1, 2, 2, 1, 2, 0, 0, 0, 2, 1, 2, 2, 1, 1,
        1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1,
        1, 1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0,
        1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1,
        1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0,
        1, 0, 0, 0, 1, 1, 2, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 0,
        1, 0, 1, 1, 1, 1, 1, 1, 2, 1, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 1,
        0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1,
        1, 1, 0, 0, 0, 1, 1, 1, 2, 0, 0, 1, 1, 1, 1, 1, 1, 1, 2, 1, 0, 2, 1, 1,
        1, 1, 2, 1, 0, 2, 1, 1, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0,
        1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1,
        0, 1, 0, 1, 1, 0, 1, 1, 0, 0, 1,

In [18]:
#c*t

In [19]:
#c * t

In [20]:
exponent[0]

tensor([ -50705.5977,  -23266.2422,  -14179.5166,  ..., -210415.6406,
        -210505.2188, -210594.7812], device='cuda:7',
       grad_fn=<SelectBackward0>)

In [15]:
import math
def irf_kernel_linear_diffusion(param, time_window=20, dt=1, eps=-90):
    """
        param[:,0] => L
        param[:,1] => D
        param[:,2] => c
    """
    L, D, c = [x.unsqueeze(-1) for x in param.t()]
    t = torch.arange(1, time_window * int(1/dt)+1, 
                     device=param.device, 
                     dtype=param.dtype)[None] * dt 
    # Hayami formula
    h = L / (2.0 * torch.sqrt(torch.pi * D * t**3))
    exponent = -((L - c * (t-dt))**2) / (4.0 * D * t)
    # Needed for numerical accuracy, to avoid nans.
    mins = torch.max(exponent,axis=1, keepdims=True).values.detach()
    exponent_ = torch.where(mins > eps, exponent, exponent / mins * eps)
    kernel = h * torch.exp(exponent_)
    # normalize
    kernel = kernel / kernel.sum(-1, keepdim=True)
    return kernel

def irf_kernel_stable_hayami(param, time_window=20, dt=1.0):
    """
    """
    L, D, c = [x.unsqueeze(-1) for x in param.t()]
    t = torch.arange(1, int(time_window * (1/dt)) + 1, 
                     device=param.device, 
                     dtype=param.dtype)[None] * dt
    # Hayami formula in log space
    logh = torch.log(L)  \
         - math.log(2.0) \
         - 0.5 * (math.log(math.pi) \
                  + torch.log(D) \
                  + 3.0 * torch.log(t))
    exponent = -((L - c * (t-dt)) ** 2) / (4.0 * D * t)
    logk = logh + exponent
    # Normalization
    logk = logk - torch.logsumexp(logk, dim=-1, keepdim=True)
    kernel = torch.exp(logk)
    return kernel

In [26]:
#model.routing_model.range

In [28]:
# params

tensor([[ 5.4900,  2.4000, 48.0000],
        [ 0.9900,  2.4000, 48.0000],
        [ 4.7700,  2.4000, 48.0000],
        ...,
        [ 0.5400,  2.4000, 48.0000],
        [ 4.2300,  2.4000, 48.0000],
        [ 1.0800,  2.4000, 48.0000]], device='cuda:7', grad_fn=<CopySlices>)

In [27]:
x = model.routing_model.router.core.aggregator(g, params)
pd.DataFrame(x.vals[x.coords[:,0]==62].cpu().detach().t()).hvplot()

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [11]:
#IRF_FN["hayami"] = irf_kernel_stable_hayami#(params, time_window=max_delay, dt=dt)

In [23]:
tr_loss.hvplot(label="training") * val_loss.hvplot(label="validation")

:Overlay
   .Curve.Training   :Curve   [index]   (0)
   .Curve.Validation :Curve   [index]   (0)

In [ ]:
xp = torch.linspace(-1,1,50, device=device)[:,None]
p_df = pd.DataFrame(model.routing_model._read_params(xp).detach().cpu(),
                     columns=["D", "c"])
p_df["c"].hvplot()

In [73]:
import matplotlib.pyplot as plt
import holoviews as hv
import hvplot.xarray

In [77]:
ps = out.view(10,10,2)

xr.DataArray(ps[...,1].detach().cpu().numpy(), 
             coords={"upa":coords_upa.numpy(), 
                     "dist":coords_dist.numpy()}).hvplot.image(x="upa", y="dist", title="celerity").opts(width=300)+\
xr.DataArray(ps[...,0].detach().cpu().numpy(), 
             coords={"upa":coords_upa.numpy(), 
                     "dist":coords_dist.numpy()}).hvplot.image(x="upa", y="dist", title="diffusivity").opts(width=300)

:Layout
   .Image.I  :Image   [upa,dist]   (value)
   .Image.II :Image   [upa,dist]   (value)

In [78]:
#plt.imshow(ps[...,1].detach().cpu().numpy())

In [79]:
#plt.imshow(ps[...,0].detach().cpu().numpy())

In [29]:
losses.hvplot()

:Curve   [index]   (0)

In [121]:
ytr, otr = extract_train(model, g, ds, init_window)
yte, ote = extract_test(model, g, ds, init_window)

1-((yte-ote)**2).mean() / yte.var()

np.float32(0.9127734)

In [45]:
self = model

In [48]:
inp = to_xtensor(x)

In [49]:
runoff_mm  = self.runoff_model(inp)
runoff_m3s = mm_to_m3s(runoff_mm, cat_area)

In [21]:
(losses).hvplot()

:Curve   [index]   (0)

In [26]:
(losses).hvplot()

:Curve   [index]   (0)

In [4]:

for irf_fn in irf_fns:
    print(irf_fn)
    res = []
    for i in range(N):
        # Init model and optimizer
        model = init_model(ds.g, 
                           inp_size=ds.X.shape[-1], 
                           dt = .25, 
                           irf_fn=irf_fn, 
                           device=device)
        opt = torch.optim.Adam([
            {'params': model.runoff_model.parameters(), 'lr': lr, 'weight_decay': wd},
            {'params': [model.routing_params], 'lr': 1e-2, 'weight_decay': 0.0}
        ])
        scheduler = torch.optim.lr_scheduler.StepLR(opt, step_size=100, gamma=0.3)

        # Train
        losses = training_loop(ds, model, opt, n_iter=n_iter, 
                               n_epoch=n_epoch, 
                               init_window=init_window,
                               scheduler=scheduler,
                               clip_grad_norm=1.0)

        # Extract and record results
        ytr, otr = extract_train(model, ds, init_window)
        yte, ote = extract_test(model, ds, init_window)
        res.append((model.cpu(), ytr, otr, yte, ote))
        
    all_results[irf_fn]=res

hayami


 78%|███████▊  | 31/40 [00:06<00:01,  4.55it/s]


KeyboardInterrupt: 

In [10]:
yte.hvplot() * ote.hvplot()

:Overlay
   .Curve.A_0.I  :Curve   [index]   (0)
   .Curve.A_0.II :Curve   [index]   (0)

In [7]:
yte

100      0.161135
101      0.158634
102      0.163706
103      0.163706
104      0.161135
           ...   
35035    0.176005
35036    0.177603
35037    0.179201
35038    0.177603
35039    0.176005
Length: 34940, dtype: float32

### Evaluation

In [ ]:
yte = {k: [x[3] for x in v] for k,v in all_results.items()}
ote = {k: [x[4] for x in v] for k,v in all_results.items()}
results = {k:pd.DataFrame([hydro_metrics(out, y) \
                           for out,y in zip(ote[k], yte[k])])
           for k in ote}

In [ ]:
{k:v.std() for k,v in results.items()}

In [ ]:
{k:v.mean() for k,v in results.items()}

In [8]:
#self = model.routing_model.router.core.aggregator

In [9]:
from diffroute.agg.kernel_aggregator import IRF_FN, aggregate_irf

In [32]:
if params is None: params = g.params
irf_fn = IRF_FN[g.irf_fn]

coords, irfs_agg = aggregate_irf( params,
                                  irf_fn=irf_fn,
                                  edges=g.edges,
                                  path_cumsum=g.path_cumsum,
                                  dt=self.dt,
                                  time_window=self.max_delay,
                                  cascade=self.cascade,
                                  include_index_diag=g.include_index_diag,
                                  block_f=self.block_f)


In [35]:
time_window=self.max_delay

In [36]:
irfs = irf_fn(params, time_window=time_window, dt=dt).squeeze()

In [42]:
param=params

In [44]:
L_vals, D_vals, c_vals = param[:, 0], param[:, 1], param[:, 2]
extended_time_steps = time_window * int(1/dt)
t_array = torch.arange(1, extended_time_steps+1, device=L_vals.device, dtype=L_vals.dtype) * dt 
L_exp, D_exp, c_exp = L_vals.unsqueeze(1), D_vals.unsqueeze(1), c_vals.unsqueeze(1)
t_exp = t_array.unsqueeze(0)
# Hayami formula
h_part = L_exp / (2.0 * torch.sqrt(torch.pi * D_exp * t_exp**3))
exponent = -((L_exp - c_exp * t_exp)**2) / (4.0 * D_exp * t_exp)
kernel = h_part * torch.exp(exponent)
# normalize
#kernel = kernel / kernel.sum(-1, keepdim=True)

In [58]:
c_exp

tensor([[100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        [100.],
        

In [57]:
t_exp

tensor([[  0.2500,   0.5000,   0.7500,   1.0000,   1.2500,   1.5000,   1.7500,
           2.0000,   2.2500,   2.5000,   2.7500,   3.0000,   3.2500,   3.5000,
           3.7500,   4.0000,   4.2500,   4.5000,   4.7500,   5.0000,   5.2500,
           5.5000,   5.7500,   6.0000,   6.2500,   6.5000,   6.7500,   7.0000,
           7.2500,   7.5000,   7.7500,   8.0000,   8.2500,   8.5000,   8.7500,
           9.0000,   9.2500,   9.5000,   9.7500,  10.0000,  10.2500,  10.5000,
          10.7500,  11.0000,  11.2500,  11.5000,  11.7500,  12.0000,  12.2500,
          12.5000,  12.7500,  13.0000,  13.2500,  13.5000,  13.7500,  14.0000,
          14.2500,  14.5000,  14.7500,  15.0000,  15.2500,  15.5000,  15.7500,
          16.0000,  16.2500,  16.5000,  16.7500,  17.0000,  17.2500,  17.5000,
          17.7500,  18.0000,  18.2500,  18.5000,  18.7500,  19.0000,  19.2500,
          19.5000,  19.7500,  20.0000,  20.2500,  20.5000,  20.7500,  21.0000,
          21.2500,  21.5000,  21.7500,  22.0000,  22

In [55]:
c_exp * t_exp

tensor([[   25.,    50.,    75.,  ...,  9950.,  9975., 10000.],
        [   25.,    50.,    75.,  ...,  9950.,  9975., 10000.],
        [   25.,    50.,    75.,  ...,  9950.,  9975., 10000.],
        ...,
        [   25.,    50.,    75.,  ...,  9950.,  9975., 10000.],
        [   25.,    50.,    75.,  ...,  9950.,  9975., 10000.],
        [   25.,    50.,    75.,  ...,  9950.,  9975., 10000.]],
       device='cuda:7', grad_fn=<MulBackward0>)

In [53]:
torch.exp(exponent)

tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]], device='cuda:7',
       grad_fn=<ExpBackward0>)

In [47]:
exponent

tensor([[   -357.3869,    -930.0565,   -1512.1589,  ..., -233296.2500,
         -233883.0781, -234469.8906],
        [   -533.8175,   -1112.1104,   -1690.7059,  ..., -230295.3281,
         -230874.0781, -231452.8281],
        [   -378.1874,    -945.2321,   -1519.2856,  ..., -229647.6250,
         -230225.1719, -230802.7344],
        ...,
        [   -561.4236,   -1147.7731,   -1734.2137,  ..., -233396.1875,
         -233982.6875, -234569.1719],
        [   -404.8432,    -982.9822,   -1566.7185,  ..., -233242.4062,
         -233828.9531, -234415.5000],
        [   -536.9062,   -1122.8428,   -1709.1443,  ..., -233369.9219,
         -233956.4062, -234542.8906]], device='cuda:7', grad_fn=<DivBackward0>)

In [46]:
h_part

tensor([[1.2005e+01, 4.2445e+00, 2.3104e+00,  ..., 1.5120e-03, 1.5063e-03,
         1.5007e-03],
        [2.1499e+00, 7.6012e-01, 4.1375e-01,  ..., 2.7077e-04, 2.6975e-04,
         2.6874e-04],
        [1.0348e+01, 3.6586e+00, 1.9915e+00,  ..., 1.3033e-03, 1.2984e-03,
         1.2935e-03],
        ...,
        [1.1805e+00, 4.1737e-01, 2.2719e-01,  ..., 1.4868e-04, 1.4812e-04,
         1.4756e-04],
        [9.2477e+00, 3.2695e+00, 1.7797e+00,  ..., 1.1647e-03, 1.1603e-03,
         1.1560e-03],
        [2.3610e+00, 8.3474e-01, 4.5438e-01,  ..., 2.9735e-04, 2.9624e-04,
         2.9513e-04]], device='cuda:7', grad_fn=<DivBackward0>)

In [40]:
#L, D, c_vals = param[:, 0], param[:, 1], param[:, 2]